# Imports and Hugging Face Login

In [1]:
!pip install huggingface-hub
!pip install datasets > delete.txt

ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2024.10.0 requires fsspec==2024.10.0, but you have fsspec 2024.9.0 which is incompatible.


In [2]:
import torch
import pickle
from huggingface_hub import hf_hub_download
from datasets import load_dataset, Image
import torch
from torch import nn, optim
from torch.utils.data import DataLoader, Dataset
import numpy as np
from geopy.distance import geodesic
import matplotlib.pyplot as plt
from torchvision import models

In [3]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(device)

cuda


In [4]:
!huggingface-cli login
# use appropiate token


    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|

    To log in, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Enter your token (input will not be visible): 
Add token as git credential? (Y/n) y
Token is valid (permission: fineGrained).
The token `CIS 5190 Project 3` has been saved to /root/.cache/huggingface/stored_tokens
Cannot authenticate through git-credential as no helper is defined on your machine.
You might have to re-au

# Models and Classes

In [9]:
class EnsembleModel(nn.Module):
    def __init__(self, models, num_models):
        super(EnsembleModel, self).__init__()
        self.models = nn.ModuleList(models)
        self.weights = nn.Parameter(torch.ones(num_models) / num_models)

    def forward(self, x):
        outputs = torch.stack([model(x) for model in self.models], dim=-1)
        weighted_output = torch.einsum('bij,j->bi', outputs, self.weights)
        return weighted_output

In [10]:
class Model1(nn.Module):
    def __init__(self, dropout):
        super(Model1, self).__init__()
        self.features = nn.Sequential(
            nn.Conv2d(3, 64, kernel_size=11, stride=4, padding=2),
            nn.ReLU(inplace=True),
            nn.MaxPool2d(kernel_size=3, stride=2),
            nn.Conv2d(64, 192, kernel_size=5, padding=2),
            nn.ReLU(inplace=True),
            nn.MaxPool2d(kernel_size=3, stride=2),
            nn.Conv2d(192, 384, kernel_size=3, padding=1),
            nn.ReLU(inplace=True),
            nn.Conv2d(384, 256, kernel_size=3, padding=1),
            nn.ReLU(inplace=True),
            nn.Conv2d(256, 256, kernel_size=3, padding=1),
            nn.ReLU(inplace=True),
            nn.MaxPool2d(kernel_size=3, stride=2),
        )
        self.classifier = nn.Sequential(
            nn.Dropout(p=dropout),
            nn.Linear(256 * 6 * 6, 1024),
            nn.ReLU(inplace=True),
            nn.Dropout(p=dropout),
            nn.Linear(1024, 512),
            nn.ReLU(inplace=True),
            nn.Linear(512, 2),
        )

    def forward(self, x):
        x = self.features(x)
        x = torch.flatten(x, 1)
        x = self.classifier(x)
        return x


def model_fn(dropout):
    return Model1(dropout)

In [11]:
class Model2(nn.Module):
    def __init__(self, num_blocks=3, dropout_rate=0.5):
        super(Model2, self).__init__()

        resnet = models.resnet34(pretrained=True)

        for param in list(resnet.parameters())[:num_blocks]:
            param.requires_grad = False

        self.features = nn.Sequential(*list(resnet.children())[:-2])
        self.avgpool = nn.AdaptiveAvgPool2d((1, 1))

        self.classifier = nn.Sequential(
            nn.Flatten(),
            nn.Dropout(p=dropout_rate),
            nn.Linear(resnet.fc.in_features, 512),
            nn.ReLU(inplace=True),
            nn.Dropout(p=dropout_rate),
            nn.Linear(512, 2)
        )

    def forward(self, x):
        x = self.features(x)
        x = self.avgpool(x)
        x = self.classifier(x)
        return x

In [12]:
class InceptionModule(nn.Module):
    def __init__(self, in_channels, ch1x1, ch3x3_reduce, ch3x3, ch5x5_reduce, ch5x5, pool_proj):
        super(InceptionModule, self).__init__()

        self.branch1 = nn.Sequential(
            nn.Conv2d(in_channels, ch1x1, kernel_size=1),
            nn.ReLU(inplace=True)
        )
        self.branch2 = nn.Sequential(
            nn.Conv2d(in_channels, ch3x3_reduce, kernel_size=1),
            nn.ReLU(inplace=True),
            nn.Conv2d(ch3x3_reduce, ch3x3, kernel_size=3, padding=1),
            nn.ReLU(inplace=True)
        )

        self.branch3 = nn.Sequential(
            nn.Conv2d(in_channels, ch5x5_reduce, kernel_size=1),
            nn.ReLU(inplace=True),
            nn.Conv2d(ch5x5_reduce, ch5x5, kernel_size=5, padding=2),
            nn.ReLU(inplace=True)
        )

        self.branch4 = nn.Sequential(
            nn.MaxPool2d(kernel_size=3, stride=1, padding=1),
            nn.Conv2d(in_channels, pool_proj, kernel_size=1),
            nn.ReLU(inplace=True)
        )

    def forward(self, x):
        branch1 = self.branch1(x)
        branch2 = self.branch2(x)
        branch3 = self.branch3(x)
        branch4 = self.branch4(x)
        outputs = torch.cat([branch1, branch2, branch3, branch4], 1)
        return outputs

class Model4(nn.Module):
    def __init__(self, dropout_rate=0.5):
        super(Model4, self).__init__()

        self.pre_layers = nn.Sequential(
            nn.Conv2d(3, 64, kernel_size=7, stride=2, padding=3),
            nn.ReLU(inplace=True),
            nn.MaxPool2d(kernel_size=3, stride=2, padding=1),
            nn.Conv2d(64, 192, kernel_size=3, padding=1),
            nn.ReLU(inplace=True),
            nn.MaxPool2d(kernel_size=3, stride=2, padding=1)
        )


        self.inception1 = InceptionModule(192, 64, 96, 128, 16, 32, 32)
        self.inception2 = InceptionModule(256, 128, 128, 192, 32, 96, 64)

        self.maxpool = nn.MaxPool2d(kernel_size=3, stride=2, padding=1)

        self.inception3 = InceptionModule(480, 192, 96, 208, 16, 48, 64)
        self.inception4 = InceptionModule(512, 160, 112, 224, 24, 64, 64)

        self.avgpool = nn.AdaptiveAvgPool2d((1, 1))
        self.classifier = nn.Sequential(
            nn.Flatten(),
            nn.Dropout(p=dropout_rate),
            nn.Linear(512, 1024),
            nn.ReLU(inplace=True),
            nn.Dropout(p=dropout_rate),
            nn.Linear(1024, 512),
            nn.ReLU(inplace=True),
            nn.Linear(512, 2)
        )

    def forward(self, x):
        x = self.pre_layers(x)
        x = self.inception1(x)
        x = self.inception2(x)
        x = self.maxpool(x)
        x = self.inception3(x)
        x = self.inception4(x)
        x = self.avgpool(x)
        x = self.classifier(x)
        return x

# Load Test Dataset

In [14]:
from torch.utils.data import Dataset
class GPSImageDataset(Dataset):
    def __init__(self, hf_dataset, transform, lat_mean=None, lat_std=None, lon_mean=None, lon_std=None):
        self.hf_dataset = hf_dataset
        self.transform = transform

        # Normalize the latitude and longitude
        self.latitudes = np.array(hf_dataset['Latitude'])
        self.longitudes = np.array(hf_dataset['Longitude'])
        self.latitude_mean = lat_mean if lat_mean is not None else self.latitudes.mean()
        self.latitude_std = lat_std if lat_std is not None else self.latitudes.std()
        self.longitude_mean = lon_mean if lon_mean is not None else self.longitudes.mean()
        self.longitude_std = lon_std if lon_std is not None else self.longitudes.std()

        self.normalized_latitudes = (self.latitudes - self.latitude_mean) / self.latitude_std
        self.normalized_longitudes = (self.longitudes - self.longitude_mean) / self.longitude_std

    def __len__(self):
        return len(self.hf_dataset)

    def __getitem__(self, idx):
        image = self.hf_dataset[idx]['image']
        latitude = self.normalized_latitudes[idx]
        longitude = self.normalized_longitudes[idx]

        if self.transform:
            image = self.transform(image)

        return image, torch.tensor([latitude, longitude], dtype=torch.float)

In [15]:
from torchvision import transforms, models
transform = transforms.Compose([
    transforms.RandomResizedCrop(224),
    transforms.RandomHorizontalFlip(),
    transforms.ColorJitter(brightness=0.2, contrast=0.2, saturation=0.2, hue=0.1),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

inference_transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

In [16]:
dataset_test = load_dataset("gydou/released_img")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/360 [00:00<?, ?B/s]

train-00000-of-00001.parquet:   0%|          | 0.00/307M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/100 [00:00<?, ? examples/s]

In [41]:
lat_mean = 39.9517411499467
lat_std = 0.0006914493505038013
lon_mean =  -75.19143213125122
lon_std =  0.0006539239061573955

test_dataset = GPSImageDataset(
    hf_dataset=dataset_test['train'],
    transform=inference_transform,
    lat_mean=lat_mean,
    lat_std=lat_std,
    lon_mean=lon_mean,
    lon_std=lon_std
)

test_dataloader = DataLoader(
    test_dataset,
    batch_size=32,
    shuffle=False,
    num_workers=4
)

# Loading Our Model from Pickle File

In [34]:
pickle_file_path = hf_hub_download(repo_id= "CIS-5190-CIA/Ensemble_Version_2", filename="ensemble_model_ver2.pkl")

In [43]:
def load_ensemble(file_name, model_classes, device="cpu"):
    """
    Load the ensemble model and individual model weights from a pickle file.

    Args:
        file_name: Path to the saved pickle file.
        model_classes: A dictionary mapping model names to their classes (e.g., {"Model1": Model1, ...}).
        device: Device to load the models onto (default is "cpu").

    Returns:
        trained_models: A dictionary of reloaded models (key -> list of models for each type).
        ensemble_weights: Numpy array of ensemble weights.
    """
    # Load the pickle file
    with open(file_name, "rb") as f:
        ensemble_data = pickle.load(f)

    # Extract the ensemble weights
    ensemble_weights = ensemble_data["ensemble_weights"]

    # Reload the individual models
    trained_models = {}
    for model_name, state_dicts in ensemble_data["models"].items():
        trained_models[model_name] = []
        for state_dict in state_dicts:
            model = model_classes[model_name]()
            model.load_state_dict(state_dict)
            model = model.to(device)
            trained_models[model_name].append(model)

    return trained_models, ensemble_weights

In [44]:
model_classes = {
    "Model1": lambda: Model1(dropout=0.5),
    "Model2": lambda: Model2(num_blocks=3, dropout_rate=0.5),
    "Model4": lambda: Model4(dropout_rate=0.5)
}

# Load the ensemble
trained_models, ensemble_weights = load_ensemble(pickle_file_path, model_classes, device="cuda")
models_ensemble = []
for model_list in trained_models.values():
    models_ensemble.extend(model_list)

# ensemble model
ensemble_model = EnsembleModel(models=models_ensemble, num_models=len(models_ensemble))
ensemble_model.weights.data = torch.tensor(ensemble_weights, dtype=torch.float32, device="cuda")
ensemble_model = ensemble_model.to("cuda")

# Evaluation

In [47]:
def evaluate_final_rmse(ensemble_model, data_loader, lat_mean, lon_mean, lat_std, lon_std):
    """
    Evaluate the ensemble model on a given dataset and compute final RMSE in meters.
    """
    ensemble_model.eval()
    total_loss = 0.0
    total_samples = 0

    with torch.no_grad():
        for images, targets in data_loader:
            images, targets = images.to(device), targets.to(device)
            outputs = ensemble_model(images)
            preds_denorm = outputs.cpu().numpy() * np.array([lat_std, lon_std]) + np.array([lat_mean, lon_mean])
            actuals_denorm = targets.cpu().numpy() * np.array([lat_std, lon_std]) + np.array([lat_mean, lon_mean])

            for pred, actual in zip(preds_denorm, actuals_denorm):
                distance = geodesic((actual[0], actual[1]), (pred[0], pred[1])).meters
                total_loss += distance ** 2
            total_samples += targets.size(0)

    final_loss = total_loss / total_samples
    final_rmse = np.sqrt(final_loss)

    return final_loss, final_rmse

In [48]:
final_test_loss, final_test_rmse = evaluate_final_rmse(
    ensemble_model=ensemble_model,
    data_loader=test_dataloader,
    lat_mean=lat_mean,
    lon_mean=lon_mean,
    lat_std=lat_std,
    lon_std=lon_std
)

print(f"Test Loss (meters^2): {final_test_loss:.2f}")
print(f"Test RMSE (meters): {final_test_rmse:.2f}")

Test Loss (meters^2): 8089.13
Test RMSE (meters): 89.94


# Visualizatoin

In [49]:
def visualize_predictions(all_preds, all_actuals, lat_mean, lon_mean, lat_std, lon_std):
    """
    Visualizes actual and predicted GPS coordinates on a scatter plot,
    including error lines connecting each prediction to its corresponding actual point.
    """

    all_preds_denorm = all_preds * np.array([lat_std, lon_std]) + np.array([lat_mean, lon_mean])
    all_actuals_denorm = all_actuals * np.array([lat_std, lon_std]) + np.array([lat_mean, lon_mean])

    plt.figure(figsize=(10, 5))

    plt.scatter(all_actuals_denorm[:, 1], all_actuals_denorm[:, 0], label='Actual', color='blue', alpha=0.6)
    plt.scatter(all_preds_denorm[:, 1], all_preds_denorm[:, 0], label='Predicted', color='red', alpha=0.6)
    for i in range(len(all_actuals_denorm)):
        plt.plot(
            [all_actuals_denorm[i, 1], all_preds_denorm[i, 1]],
            [all_actuals_denorm[i, 0], all_preds_denorm[i, 0]],
            color='gray', linewidth=0.5
        )

    plt.legend()
    plt.xlabel('Longitude')
    plt.ylabel('Latitude')
    plt.title('Actual vs. Predicted GPS Coordinates with Error Lines')
    plt.grid(True)
    plt.show()

In [ ]:
ensemble_model.eval()

all_preds = []
all_actuals = []

with torch.no_grad():
    for images, targets in test_dataloader:
        images = images.to("cuda")
        targets = targets.to("cuda")

        preds = ensemble_model(images)

        all_preds.append(preds.cpu().numpy())
        all_actuals.append(targets.cpu().numpy())

all_preds = np.concatenate(all_preds, axis=0)
all_actuals = np.concatenate(all_actuals, axis=0)

visualize_predictions(
    all_preds=all_preds,
    all_actuals=all_actuals,
    lat_mean=lat_mean,
    lon_mean=lon_mean,
    lat_std=lat_std,
    lon_std=lon_std
)